In [ ]:
import numpy as np
import pandas as pd
import seaborn as sns
import matplotlib.pyplot as plt

import transformers
from transformers import AutoTokenizer, AutoModel,AdamW
import torch
import torch.nn.functional as F
from transformers import AutoModelForSequenceClassification

import nltk
from nltk.corpus import stopwords
from nltk.stem.porter import PorterStemmer
from wordcloud import WordCloud,STOPWORDS
from nltk.stem import WordNetLemmatizer
from nltk.tokenize import word_tokenize,sent_tokenize
import re,string,unicodedata

from sklearn.model_selection import train_test_split
from string import punctuation
from nltk.corpus import wordnet

import warnings
warnings.filterwarnings('ignore')

In [ ]:
pip install transformers

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 6.8/6.8 MB 46.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 7.8/7.8 MB 81.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 200.1/200.1 KB 17.9 MB/s eta 0:00:00


In [ ]:

from sklearn.metrics.pairwise import cosine_similarity

In [ ]:
df = pd.read_csv("resume.csv")

In [ ]:
df.head()

Category                                             Resume
0  Data Science  Skills * Programming Languages: Python (pandas...
1  Data Science  Education Details \r\nMay 2013 to May 2017 B.E...
2  Data Science  Areas of Interest Deep Learning, Control Syste...
3  Data Science  Skills â¢ R â¢ Python â¢ SAP HANA â¢ Table...
4  Data Science  Education Details \r\n MCA   YMCAUST,  Faridab...

In [ ]:
#from sklearn.preprocessing import LabelEncoder
#le = LabelEncoder()

In [ ]:
#df['labels'] = df['Category'].astype('category')

In [ ]:
df.Category.unique()

array(['Data Science', 'HR', 'Advocate', 'Arts', 'Web Designing',
       'Mechanical Engineer', 'Sales', 'Health and fitness',
       'Civil Engineer', 'Java Developer', 'Business Analyst',
       'SAP Developer', 'Automation Testing', 'Electrical Engineering',
       'Operations Manager', 'Python Developer', 'DevOps Engineer',
       'Network Security Engineer', 'PMO', 'Database', 'Hadoop',
       'ETL Developer', 'DotNet Developer', 'Blockchain', 'Testing'],
      dtype=object)

In [ ]:
py = df[df['Category'] == 'Python Developer']

In [ ]:
sa = df[df['Category'] == 'Sales']
sa.head()

Category                                             Resume
225    Sales  Education Details \r\n Bachelor's   \r\n Bache...
226    Sales  SKILLS 1. MS-Office 2. Good Communication skil...
227    Sales  KEY SKILLS: â¢ Planning & Strategizing â¢ Pr...
228    Sales  IT Skills: MS Office. Photoshop. SQL Server.Ed...
229    Sales  Skill Sets: â¢ Multi-tasking â¢ Collaborativ...

In [ ]:
civ = df[df['Category'] == 'Civil Engineer']
civ.head()

Category                                             Resume
295  Civil Engineer  Education Details \r\n B.E in Civil Engineerin...
296  Civil Engineer  Education Details \r\nJanuary 2005 S.S.C  Bara...
297  Civil Engineer  SKILLS â¢ 1.Autocad â¢ 2.Pro v â¢ 3.Catia â...
298  Civil Engineer  Computer Skills â¢ Holder of valid KSA licens...
299  Civil Engineer  COMPUTER KNOWLEDGE â¢ Drafting tools: AutoCAD...

In [ ]:
ee = df[df['Category'] == 'Electrical Engineering']
ee.head()

Category                                             Resume
481  Electrical Engineering  Skills: 1) MC Office 2) AutoCAD 2016 3) Introd...
482  Electrical Engineering  Education Details \r\n\r\nElectrical engineeri...
483  Electrical Engineering  â¢ Achievement oriented with people managemen...
484  Electrical Engineering  Education Details \r\nJuly 2016 to May 2019 BE...
485  Electrical Engineering  Education Details \r\nJanuary 2012 to January ...

In [ ]:
me = df[df['Category'] == 'Mechanical Engineer']
me.head()

Category                                             Resume
185  Mechanical Engineer  Education Details \r\nMay 1999 to September 20...
186  Mechanical Engineer  SKILLS: â¢ Knowledge of software / computer: ...
187  Mechanical Engineer  Education Details \r\nJanuary 2018 Bachelor's ...
188  Mechanical Engineer  Education Details \r\nJune 2014 to June 2018 B...
189  Mechanical Engineer  * I'm hard working person. * I'm self confiden...

In [ ]:
ba = df[df['Category'] == 'Business Analyst']
ba.head()

Category                                             Resume
403  Business Analyst  Education Details \r\n BE Computer Science Mum...
404  Business Analyst  Technical Skills Application Servers: IIS 6.0,...
405  Business Analyst  Key Skills - Requirement Gathering - Requireme...
406  Business Analyst  IT Skills: Area Exposure Modeling Tool: Bizagi...
407  Business Analyst  TECHNOLOGICAL SKILLS â¦ Knowledge of Computer...

In [ ]:
py.head()

Category                                             Resume
551  Python Developer  Technical Skills / Responsibilities: â¢ Hands...
552  Python Developer  Education Details \r\nJune 2013 to June 2016 D...
553  Python Developer  TECHNICAL PROFICIENCIES Platform: Ubuntu/Fedor...
554  Python Developer  Technical Skills: Languages Python Python Fram...
555  Python Developer  Training attended: 1. Successfully completed E...

In [ ]:
df.shape

(962, 2)

In [ ]:
df.isnull().sum()

Category    0
Resume      0
dtype: int64

In [ ]:
df['Resume'] = df['Resume'].str.lower()
df.Resume[0]

'skills * programming languages: python (pandas, numpy, scipy, scikit-learn, matplotlib), sql, java, javascript/jquery. * machine learning: regression, svm, naã¯ve bayes, knn, random forest, decision trees, boosting techniques, cluster analysis, word embedding, sentiment analysis, natural language processing, dimensionality reduction, topic modelling (lda, nmf), pca & neural nets. * database visualizations: mysql, sqlserver, cassandra, hbase, elasticsearch d3.js, dc.js, plotly, kibana, matplotlib, ggplot, tableau. * others: regular expression, html, css, angular 6, logstash, kafka, python flask, git, docker, computer vision - open cv and understanding of deep learning.education details \r\n\r\ndata science assurance associate \r\n\r\ndata science assurance associate - ernst & young llp\r\nskill details \r\njavascript- exprience - 24 months\r\njquery- exprience - 24 months\r\npython- exprience - 24 monthscompany details \r\ncompany - ernst & young llp\r\ndescription - fraud investigatio

In [ ]:
resume = []
for sen in df['Resume']:
  text = re.sub(r'[^a-zA-Z0-9\s]', '', sen)
  resume.append(text)

In [ ]:
 resume[0]

'skills  programming languages python pandas numpy scipy scikitlearn matplotlib sql java javascriptjquery  machine learning regression svm nave bayes knn random forest decision trees boosting techniques cluster analysis word embedding sentiment analysis natural language processing dimensionality reduction topic modelling lda nmf pca  neural nets  database visualizations mysql sqlserver cassandra hbase elasticsearch d3js dcjs plotly kibana matplotlib ggplot tableau  others regular expression html css angular 6 logstash kafka python flask git docker computer vision  open cv and understanding of deep learningeducation details \r\n\r\ndata science assurance associate \r\n\r\ndata science assurance associate  ernst  young llp\r\nskill details \r\njavascript exprience  24 months\r\njquery exprience  24 months\r\npython exprience  24 monthscompany details \r\ncompany  ernst  young llp\r\ndescription  fraud investigations and dispute services   assurance\r\ntechnology assisted review\r\ntar te

In [ ]:
from nltk.corpus import stopwords
lemmatizer = WordNetLemmatizer()
nltk.download('stopwords')
nltk.download('punkt')
nltk.download('wordnet')
nltk.download('omw-1.4')
stops = set(stopwords.words("english"))

[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Unzipping corpora/stopwords.zip.
[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Unzipping tokenizers/punkt.zip.
[nltk_data] Downloading package wordnet to /root/nltk_data...
[nltk_data] Downloading package omw-1.4 to /root/nltk_data...


In [ ]:
def identify_tokens(row):
    review = row
    tokens = nltk.word_tokenize(review)
    # taken only words (not punctuation)
    token_words = [w for w in tokens if w.isalpha()]
    meaningful_words = [w for w in token_words if not w in stops]
    lemmatize_list = [lemmatizer.lemmatize(word) for word in meaningful_words]
    joined_words = (' '.join(lemmatize_list))
    return joined_words

In [ ]:
df['Resume'] = df['Resume'].apply(identify_tokens)

In [ ]:
df.head()

Category                                             Resume
0  Data Science  skill programming language python panda numpy ...
1  Data Science  education detail may may data scientist data s...
2  Data Science  area interest deep learning control system des...
3  Data Science  skill r python sap hana tableau sap hana sql s...
4  Data Science  education detail mca ymcaust faridabad haryana...

In [ ]:
df.Resume[0]

'skill programming language python panda numpy scipy matplotlib sql java machine learning regression svm bayes knn random forest decision tree boosting technique cluster analysis word embedding sentiment analysis natural language processing dimensionality reduction topic modelling lda nmf pca neural net database visualization mysql sqlserver cassandra hbase elasticsearch plotly kibana matplotlib ggplot tableau others regular expression html cs angular logstash kafka python flask git docker computer vision open cv understanding deep detail data science assurance associate data science assurance associate ernst young llp skill detail exprience month exprience month exprience monthscompany detail company ernst young llp description fraud investigation dispute service assurance technology assisted review tar technology assisted review assist accelerating review process run analytics generate report core member team helped developing automated review platform tool scratch assisting e discov

In [ ]:
import pandas as pd
from collections import Counter

# Function to count word frequency in a string
def count_words(text):
    words = text.split()
    return Counter(words)

# Apply the function to the column of the dataset
df['word_frequency'] = df['Resume'].apply(count_words)


In [ ]:
df.head()

Category                                             Resume  \
0  Data Science  skill programming language python panda numpy ...   
1  Data Science  education detail may may data scientist data s...   
2  Data Science  area interest deep learning control system des...   
3  Data Science  skill r python sap hana tableau sap hana sql s...   
4  Data Science  education detail mca ymcaust faridabad haryana...   

                                      word_frequency  
0  {'skill': 2, 'programming': 1, 'language': 3, ...  
1  {'education': 1, 'detail': 3, 'may': 2, 'data'...  
2  {'area': 1, 'interest': 1, 'deep': 1, 'learnin...  
3  {'skill': 2, 'r': 5, 'python': 4, 'sap': 17, '...  
4  {'education': 1, 'detail': 3, 'mca': 1, 'ymcau...

In [ ]:
df.word_frequency[187]

Counter({'education': 1,
         'detail': 3,
         'january': 1,
         'bachelor': 1,
         'engineering': 6,
         'mumbai': 1,
         'maharashtra': 2,
         'mgm': 1,
         'college': 1,
         'diploma': 1,
         'mechanical': 4,
         'pune': 2,
         'mit': 2,
         'president': 3,
         'student': 3,
         'association': 3,
         'skill': 1,
         'company': 3,
         'full': 1,
         'throttle': 1,
         'description': 2,
         'conducted': 2,
         'iit': 1,
         'bombay': 1,
         'worked': 1,
         'mesa': 1,
         'car': 1,
         'race': 1,
         'stepcone': 1,
         'paper': 1,
         'project': 1,
         'contest': 1,
         'exhibition': 1,
         'gmr': 1,
         'instiute': 1,
         'technology': 1})

In [ ]:
df['word_frequency'][0]['skill']

2

In [ ]:
word_counts = Counter()
for i in range(len(df)):
    word_counts.update(count_words(df['Resume'][i]))


In [ ]:
most_common_word = word_counts.most_common(1)[0][0]
print('The most common word is:', most_common_word)

The most common word is: project


In [ ]:
top_words = word_counts.most_common(50)
print('Top 50 most common words:')
for word, count in top_words:
    print(f'{word}: {count}')

Top 50 most common words:
project: 3884
exprience: 3829
company: 3613
month: 3344
detail: 3132
description: 3122
team: 2126
data: 2125
skill: 2048
management: 1930
system: 1888
year: 1495
maharashtra: 1449
database: 1442
client: 1415
application: 1386
technology: 1354
service: 1344
business: 1272
test: 1266
testing: 1264
requirement: 1249
report: 1240
le: 1217
development: 1180
developer: 1169
customer: 1155
process: 1145
responsibility: 1133
server: 1131
using: 1124
january: 1090
work: 1038
engineering: 1035
pune: 1019
role: 950
java: 917
sql: 912
ltd: 899
software: 888
user: 860
pvt: 831
operation: 829
activity: 795
environment: 765
technical: 755
sale: 753
monthscompany: 746
working: 745
university: 745


In [ ]:
words_to_remove = ['university','monthscompany','working','pvt','user','ltd','work','january','engineering','using','responsibility','le'
'testing','application','maharashtra','year','skill','data','team','description','detail','month','company','exprience','project'

]

In [ ]:
df['Resume'] = df['Resume'].apply(lambda x: ' '.join([word for word in x.split() if word.lower() not in words_to_remove]))

In [ ]:
df['Resume'][0]

'programming language python panda numpy scipy matplotlib sql java machine learning regression svm bayes knn random forest decision tree boosting technique cluster analysis word embedding sentiment analysis natural language processing dimensionality reduction topic modelling lda nmf pca neural net database visualization mysql sqlserver cassandra hbase elasticsearch plotly kibana matplotlib ggplot tableau others regular expression html cs angular logstash kafka python flask git docker computer vision open cv understanding deep science assurance associate science assurance associate ernst young llp ernst young llp fraud investigation dispute service assurance technology assisted review tar technology assisted review assist accelerating review process run analytics generate report core member helped developing automated review platform tool scratch assisting e discovery domain tool implement predictive coding topic modelling automating review resulting reduced labor cost time spent lawyer

In [ ]:
df.head()

Category                                             Resume  \
0  Data Science  programming language python panda numpy scipy ...   
1  Data Science  education may may scientist scientist matelabs...   
2  Data Science  area interest deep learning control system des...   
3  Data Science  r python sap hana tableau sap hana sql sap han...   
4  Data Science  education mca ymcaust faridabad haryana scienc...   

                                      word_frequency  
0  {'skill': 2, 'programming': 1, 'language': 3, ...  
1  {'education': 1, 'detail': 3, 'may': 2, 'data'...  
2  {'area': 1, 'interest': 1, 'deep': 1, 'learnin...  
3  {'skill': 2, 'r': 5, 'python': 4, 'sap': 17, '...  
4  {'education': 1, 'detail': 3, 'mca': 1, 'ymcau...

In [ ]:
#data_texts = df['Resume'].to_list()

#data_labels = df['encoded_text'].to_list()

In [ ]:
import pandas as pd
import numpy as np
import tensorflow as tf
from sklearn.model_selection import train_test_split
from transformers import RobertaTokenizer, TFRobertaForSequenceClassification, TFTrainer, TFTrainingArguments


In [ ]:
train_texts, val_texts = train_test_split(df['Resume'], test_size=0.2, random_state=42)

In [ ]:
len(train_texts)
len(val_texts)

193

In [ ]:
tokenizer = RobertaTokenizer.from_pretrained('Maite89/Roberta_finetuning_semantic_similarity_stsb_multi_mt')
train_encodings = tokenizer(train_texts.tolist(),max_length = 512, truncation=True, padding=True)
val_encodings = tokenizer(val_texts.tolist(),max_length = 512, truncation=True, padding=True)

In [ ]:
train_encodings

{'input_ids': [[0, 4168, 130, 1507, 7873, 28302, 38472, 536, 27307, 33466, 3407, 138, 35918, 132, 21813, 352, 10666, 3251, 19765, 1805, 13261, 319, 326, 35887, 2056, 126, 359, 389, 27062, 1805, 17521, 725, 397, 4783, 13885, 854, 445, 48701, 334, 2068, 423, 666, 636, 13261, 319, 555, 3590, 2014, 1507, 1466, 15399, 327, 35918, 132, 21813, 2774, 2991, 35918, 132, 21813, 401, 514, 435, 401, 723, 138, 17888, 5656, 126, 457, 12257, 655, 13743, 326, 17340, 6539, 2657, 2888, 10990, 2991, 11307, 1150, 319, 6539, 2657, 2888, 10990, 2991, 11307, 1150, 319, 35918, 551, 126, 2549, 393, 35918, 551, 126, 2549, 393, 32873, 3809, 2991, 1998, 138, 489, 4794, 24522, 401, 138, 27855, 6107, 1253, 121, 3264, 1202, 401, 138, 980, 319, 3251, 31310, 23291, 1890, 757, 31310, 23291, 2282, 2423, 9988, 1890, 757, 14010, 475, 2991, 8106, 25123, 1594, 329, 14459, 2021, 25203, 324, 355, 35981, 1571, 1202, 34007, 42708, 424, 19818, 8344, 14878, 137, 2244, 46240, 31310, 23291, 1890, 757, 637, 33271, 1061, 6093, 143, 90

In [ ]:
np.zeros(len(train_encodings))

array([0., 0.])

In [ ]:
# Create TensorFlow datasets
train_dataset = tf.data.Dataset.from_tensor_slices((
    dict(train_encodings),
    np.zeros(769)
))
val_dataset = tf.data.Dataset.from_tensor_slices((
    dict(val_encodings),
    np.zeros(193)
))

In [ ]:
model = TFRobertaForSequenceClassification.from_pretrained('Maite89/Roberta_finetuning_semantic_similarity_stsb_multi_mt',from_pt=True, num_labels=1)

Some weights of the PyTorch model were not used when initializing the TF 2.0 model TFRobertaForSequenceClassification: ['embeddings.position_ids']
- This IS expected if you are initializing TFRobertaForSequenceClassification from a PyTorch model trained on another task or with another architecture (e.g. initializing a TFBertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing TFRobertaForSequenceClassification from a PyTorch model that you expect to be exactly identical (e.g. initializing a TFBertForSequenceClassification model from a BertForSequenceClassification model).
Some weights or buffers of the TF 2.0 model TFRobertaForSequenceClassification were not initialized from the PyTorch model and are newly initialized: ['classifier.dense.weight', 'classifier.dense.bias', 'classifier.out_proj.weight', 'classifier.out_proj.bias']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and 

In [ ]:
# Define the training arguments
training_args = TFTrainingArguments(
    output_dir='./results',
    num_train_epochs=5,
    per_device_train_batch_size=16,
    per_device_eval_batch_size=64,
    warmup_steps=500,
    weight_decay=0.01,
    logging_dir='./logs',
    logging_steps=1000,
    evaluation_strategy='steps',
    eval_steps=1000,
    #load_best_model_at_end=True,
    metric_for_best_model='eval_loss',
    greater_is_better=False
)

In [ ]:
trainer = TFTrainer(
    model=model,
    args=training_args,
    train_dataset=train_dataset,
    eval_dataset=val_dataset,
    compute_metrics=tf.keras.metrics.mean_squared_error
)

In [ ]:
trainer.train()

ValueError: ignored

In [ ]:
tokenizer1 = AutoTokenizer.from_pretrained(model_name2)

In [ ]:
from transformers import TFRobertaModel

In [ ]:
model2 = AutoModel.from_pretrained(model_name2)

In [ ]:
from sklearn.utils import shuffle
X, y = shuffle(X, y, random_state=42)

In [ ]:
from sklearn.model_selection import train_test_split
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size = 0.20, random_state = 0,stratify=y)

In [ ]:
train_encodings = tokenizer1(X_train, truncation=True, padding=True)
test_encodings = tokenizer1(X_test, truncation=True, padding=True)

In [ ]:
import tensorflow as tf

train_dataset = tf.data.Dataset.from_tensor_slices((
    dict(train_encodings),
    y_train
))

test_dataset = tf.data.Dataset.from_tensor_slices((
    dict(test_encodings),
    y_test
))

In [ ]:
train_dataset

<_TensorSliceDataset element_spec=({'input_ids': TensorSpec(shape=(512,), dtype=tf.int32, name=None), 'attention_mask': TensorSpec(shape=(512,), dtype=tf.int32, name=None)}, TensorSpec(shape=(), dtype=tf.int32, name=None))>

In [ ]:
train_encodings

{'input_ids': [[0, 35918, 132, 3301, 823, 340, 424, 452, 838, 2061, 2556, 1324, 1462, 1571, 556, 7196, 317, 326, 1961, 1202, 352, 5136, 562, 343, 2657, 2888, 911, 121, 9988, 2657, 2888, 9814, 2657, 2888, 3401, 2888, 326, 44328, 907, 6081, 141, 48470, 18004, 119, 1462, 16224, 19924, 326, 45597, 17606, 403, 326, 325, 9761, 529, 16558, 34060, 490, 6345, 373, 130, 331, 2064, 343, 35918, 132, 21813, 352, 137, 121, 876, 125, 12257, 326, 16310, 1684, 1113, 846, 13143, 1197, 585, 1329, 1571, 328, 1329, 35056, 848, 28924, 326, 137, 121, 876, 125, 12257, 326, 16310, 1684, 1113, 490, 10103, 313, 21308, 544, 490, 10103, 313, 21308, 544, 377, 21200, 5382, 373, 1358, 10793, 12386, 343, 1853, 35981, 911, 121, 9988, 377, 21200, 5382, 373, 1358, 10793, 12386, 343, 1853, 35981, 876, 125, 12257, 356, 4689, 12897, 44769, 15540, 326, 44328, 5337, 49542, 489, 4794, 24522, 2556, 1324, 1462, 49920, 2991, 37441, 4067, 2020, 490, 10103, 326, 1961, 1202, 352, 5136, 562, 343, 1147, 4689, 10959, 26667, 547, 4509, 

In [ ]:
from transformers import TFDistilBertForSequenceClassification, TFTrainer, TFTrainingArguments

training_args = TFTrainingArguments(
    output_dir='./results',          # output directory
    num_train_epochs=2,              # total number of training epochs
    per_device_train_batch_size=8,  # batch size per device during training
    per_device_eval_batch_size=16,   # batch size for evaluation
    warmup_steps=500,                # number of warmup steps for learning rate scheduler
    weight_decay=0.01,               # strength of weight decay
    logging_dir='./logs',            # directory for storing logs
    logging_steps=10,
)

In [ ]:
from transformers import TFRobertaModel

In [ ]:
with training_args.strategy.scope():
    model2 = TFRobertaModel.from_pretrained(model_name2,from_pt=True)

trainer = TFTrainer(
    model=model2,                         # the instantiated 🤗 Transformers model to be trained
    args=training_args,                  # training arguments, defined above
    train_dataset=train_dataset,         # training dataset
    eval_dataset=test_dataset             # evaluation dataset
)

trainer.train()

Some weights of the PyTorch model were not used when initializing the TF 2.0 model TFRobertaModel: ['embeddings.position_ids']
- This IS expected if you are initializing TFRobertaModel from a PyTorch model trained on another task or with another architecture (e.g. initializing a TFBertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing TFRobertaModel from a PyTorch model that you expect to be exactly identical (e.g. initializing a TFBertForSequenceClassification model from a BertForSequenceClassification model).
All the weights of TFRobertaModel were initialized from the PyTorch model.
If your task is similar to the task the model of the checkpoint was trained on, you can already use TFRobertaModel for predictions without further training.


ValueError: ignored

In [ ]:
tokenized_resume2 = []
for words in df.Resume:
  tokens1 = tokenizer1(words, padding = True, truncation = True, max_length = 512, return_tensors = "pt")
  tokenized_resume2.append(tokens1)

In [ ]:
embedding12 = tokenized_resume2[575]
embedding22 = tokenized_resume2[404]

In [ ]:
with torch.no_grad():
    resume1_embedding2 = model2(**embedding12)[0].mean(dim=1)
    resume2_embedding2 = model2(**embedding22)[0].mean(dim=1)

In [ ]:
similarity2 = F.cosine_similarity(resume1_embedding2, resume2_embedding2)
print(similarity2.item())

0.8453418612480164


In [ ]:
tokenized_resume2[2]

{'input_ids': tensor([[    0, 45866,  1502,   138,   313,  1037,   536, 27307,  1860,   326,
         44328,  8175,  2244, 25869,  1584,   359,  6968, 17868,   143,  1061,
           313, 21308,   134,  9801,  5519,   143, 16835, 35918,   132,  3301,
          1157,  4783,  4302,   352,  2549,   423,   449,  9768,   745,   139,
         16835,  1853, 35981,  1564,  4203,  5829,   907, 18105,  1396,   354,
          5439,  3935,   126, 32545, 11307,  1150,   319,   637,   609,  7249,
          1462,   363, 39691, 19818, 47881, 35918,   132,  3301,  2244, 25869,
           551, 31073,   406,   316,   143, 37978,   490, 10103,  1593, 28769,
           316,   143, 37978,   363,   621,   129,  2556,  1324,  1462,   399,
          8285,   843,   399,   628,  2207,   126,   994,  4383,   403, 38884,
          3210,  3715,  5170,   134,   316,   143, 37978,  6539, 18004,   119,
          1462,   316,   143,  2396,   131,   490, 10103,  3401,  2888,   326,
         44328,   907,  6081,   141,  

In [ ]:
torch.tensor(tokenized_resume2[0]['input_ids'])

tensor([[    0,  2244, 25869,  2556,  1324,  1462,   316,   143, 37978, 39219,
         19960,   486,   143,   326,   782,   143,   551,   138,   134, 18817,
         16777,   326, 45597,   490, 10103,  6968,  1150,   536, 27307,  3961,
         14466,   326,   140,   131,   401,   913,   321,  1571, 21756,  6377,
         34007,  9484,   138,  9496,   567,  4182,   123,  1684,   315,  2888,
         35918,   132,  3474,   921, 34609,  5519,  4880,   357, 43201,  5074,
           424, 25123,  1485,  9801,  5519,  4880,   357,  2197,  2556,  1324,
          1462,  2917, 37595, 40463,  2451,  4783, 12086,  2991, 45261,  1002,
          1538,  1202,   314,   459,   356,   131,   124,   316,   446,  1082,
          2957, 24507, 16224, 19924,  7748,  3325,  2991,   333,  4880, 45597,
           326, 45597,  9688,   762,   601,   137, 15845,   352, 19924, 30307,
           636,   492, 20622,   316, 18817,  3251,  1571,   453,   602,   551,
           138,   134, 18817, 16777,   399,   125,  

In [ ]:
input_ids = [d['input_ids'] for d in tokenized_resume2]
attention_mask = [e['attention_mask'] for e in tokenized_resume2]


In [ ]:
type(input_ids[0])

torch.Tensor

In [ ]:
len(input_ids)

962

In [ ]:
train_dataset = torch.utils.data.TensorDataset(
    input_ids,
    attention_mask,
    a)

AttributeError: ignored

In [ ]:
model_name3 = 'bert-large-uncased'

In [ ]:
tokenizer2 = AutoTokenizer.from_pretrained(model_name3)

In [ ]:
model3 = AutoModel.from_pretrained(model_name3)

Some weights of the model checkpoint at bert-large-uncased were not used when initializing BertModel: ['cls.predictions.transform.dense.bias', 'cls.predictions.decoder.weight', 'cls.predictions.bias', 'cls.predictions.transform.dense.weight', 'cls.predictions.transform.LayerNorm.bias', 'cls.seq_relationship.bias', 'cls.seq_relationship.weight', 'cls.predictions.transform.LayerNorm.weight']
- This IS expected if you are initializing BertModel from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing BertModel from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).


In [ ]:
tokenized_resume3 = []
for words in df.Resume:
  tokens2 = tokenizer2(words, padding = True, truncation = True, max_length = 512, return_tensors = "pt")
  tokenized_resume3.append(tokens2)

In [ ]:
embedding13 = tokenized_resume3[297]
embedding23 = tokenized_resume3[482]

In [ ]:
with torch.no_grad():
    resume1_embedding3 = model3(**embedding13)[0].mean(dim=1)
    resume2_embedding3 = model3(**embedding23)[0].mean(dim=1)

In [ ]:
similarity3 = F.cosine_similarity(resume1_embedding3, resume2_embedding3)
print(similarity3.item())

0.8140127062797546
